In [2]:
import re, copy, csv
from collections import defaultdict
from tqdm import tqdm
import pandas as pd
from xml.dom.minicompat import NodeList
from anytree import Node, RenderTree, PostOrderIter, PreOrderIter
from sklearn.model_selection import train_test_split

In [3]:
TARGET_LEVEL = 8

global dict_lvl
dict_lvl = {1: -3, 3: -2, 4: -1, 6: 0}

def convert_to_int(x):
    lvl = x['lvl']
    try:
        return int(lvl)
    except ValueError:
        title = x['title']
        if len(title) == 1:
            return -3
        elif len(title) == 3:
            return -2
        elif len(title) == 4:
            return -1

In [4]:
import spacy
from spacy import displacy
from spacy.symbols import NOUN,VERB,ADJ
from spacy.tokenizer import Tokenizer

In [5]:
!python3 -m spacy info


============================== Info about spaCy ==============================

spaCy version    3.2.0                         
Location         /usr/local/lib/python3.9/site-packages/spacy
Platform         macOS-10.15.7-x86_64-i386-64bit
Python version   3.9.9                         
Pipelines        en_core_web_sm (3.2.0), en_core_web_trf (3.2.0), zh_core_web_trf (3.2.0), zh_core_web_sm (3.2.0)



In [89]:
nlpEN = spacy.load("en_core_web_sm")

In [96]:
docEN = nlpEN("NATURAL OR MAN-MADE THREADS OR FIBRES")
#"Facilitating engagement of lifting-hooks with draw-knives", "Removing yarn from centrifugal cups on to yarn carriers", "Rendering uniform or evening non-uniform features", "Modifying the surface", "Separating or spreading"
"""
for chunk in docEN.noun_chunks:
    print(chunk.text, chunk.root.text, chunk.root.dep_,
            chunk.root.head.text)
"""
for token in docEN:
    print(token.text,token.dep_,token.head,token.head.dep_)
displacy.render(docEN, style='dep', jupyter=True)

NATURAL amod MADE compound
OR cc NATURAL amod
MAN compound MADE compound
- punct MADE compound
MADE compound THREADS ROOT
THREADS ROOT THREADS ROOT
OR cc THREADS ROOT
FIBRES conj THREADS ROOT


In [24]:
#!python3 -m spacy download zh_core_web_sm
nlpZH = spacy.load('zh_core_web_sm')

DEPRECATION: Configuring installation scheme with distutils config files is deprecated and will no longer work in the near future. If you are using a Homebrew or Linuxbrew Python, please see discussion at https://github.com/Homebrew/homebrew-core/issues/76621
     |████████████████████████████████| 49.5 MB 6.0 MB/s             
You should consider upgrading via the '/usr/local/opt/python@3.9/bin/python3.9 -m pip install --upgrade pip' command.
✔ Download and installation successful
You can now load the package via spacy.load('zh_core_web_sm')


In [98]:
docZH = nlpZH("已用或未用的胶片长度的计量或指示")
for token in docZH:
    print(token.text,token.dep_,token.head,token.head.dep_)
"""
for chunk in docZH.noun_chunks:
    print(chunk.text, chunk.root.text, chunk.root.dep_,
            chunk.root.head.text)
"""
displacy.render(docZH, style='dep', jupyter=True)

已 advmod 用 ROOT
用 ROOT 用 ROOT
或 cc 用 ROOT
未 advmod 用 conj
用 conj 用 ROOT
的 mark 用 conj
胶片 ccomp 用 conj
长度 dobj 胶片 ccomp
的 mark 胶片 ccomp
计量 dobj 用 conj
或 cc 用 ROOT
指示 conj 用 ROOT


In [1]:
detail_list = ["details","structural details","constructional details","component parts","component parts or constructional details","constructional details or arrangements","constructional arrangements","accessories","details or accessories","details; accessories","details or accessories"]

In [6]:
def clean_descr_EN(description):
    """
    1. remove references from the description, such as *** (preserving A23B; obtaining protein compositions for foodstuffs A23J1/00;)
    2. remove '{' and '}'
    3. remove i.e. ***
        EXCEPTIONS: 
            1) followed by simple NOUN phrase after 
                A61F7/03	2	thermophore, i.e. self-heating	载热体，即自加热
                A61K31/4415	5	Pyridoxine, i.e.vitamin B 6	吡哆醇，即维生素B6
                A61L2/14	2	Plasma, i.e. ionised gases	等离子体，即离子化气体
                H01C7/10	1	voltage responsive, i.e. varistors	电压响应的，即压敏电阻器
containing ";" or "e.g."
                A61K31/455	5	Nicotinic acid, i.e. niacin; Derivatives thereof, e.g. esters, amides	烟酸，即烟碱酸；其衍生物，例如酯，酰胺
            3) "即" in Chinese, but translated from "e.g."
                D03C1/36	2	Card- or chain-saving arrangements, e.g. cross-border dobbies	纹板或纹链的节省装置，即:织横边多臂机
                D03D39/10	1	Wire-tapestry looms, e.g. for weaving velvet or Brussels or Wilton carpets, the pile being formed over weftwise wires	钢丝起绒花毯织机，即在纬向金属丝上起绒头的立绒，如布鲁塞尔式或摩尔顿式地毯的织机
    4. remove explications in "（" and "）"
        D21F1/66	1	Pulp catching, de-watering, or recovering; Re-use of pulp-water	纸浆捕集、脱水及回收；浆水（即白水）再用
        供灵缇（一种身体细长的跑狗）
    """
    #description = description.replace('{', '').replace('}','')
    description = re.sub(r'\ ?\([\w\W]*([A-Z]{1}[0-9]{2}[A-Z]{1}[0-9]*[\/]*[0-9]*)*[\w\W]*\)', '', description)

    #description = re.sub(r'[ ,]*i\.e\..*', '', description)  >>>>>> after separation by semicolon
    
    ######EN: explication in "(" and ")"
    description = re.sub(r'\(.+\)', '', description)
    
    return description#.lower()


def clean_descr_ZH(description):
    """
    """
    description = re.sub(r'\ ?\([\w\W]*([A-Z]{1}[0-9]{2}[A-Z]{1}[0-9]*[\/]*[0-9]*)*[\w\W]*\)', '', description)
    
    ######ZH: "i.e." ==> "即"
    #description = re.sub(r'[ ，]*即.*', '', description)  >>>>>> after separation by semicolon
    
    ######ZH: explication in "（" and "）"
    description = re.sub(r'（.+）', '', description)
    #description = re.sub(r'（[^\u4e00-\u9fa5]+）', '', description)
    """
    0) To replace
        A01B49/00	0	Combined machines (auxiliary devices attached to machines of a different kind, e.g. harrows attached to ploughs, see the relevant groups for the machines)	联合作业机械（联接在不同类型机具上的附属部件，比如联接在犁上的耙，见机具的各有关组）
        A01B79/00	0	Methods for working soil (essentially requiring the use of particular machines, see the relevant groups for the machines)	整地方法必须使用的专用机械见该机械的各相应组）
    
    1)[ZH] Translation in () 
        G10D_17/00 Musical instruments not provided for in any other group of this subclass, e.g. Aeolian harp, singing-flame musical instrument 本小类其他各组中不包含的乐器，例如风弦琴（aeolian harp），歌焰乐器（singing-flame musical instrument）
    2)[ZH] e.g.
        G10L_15/22 Procedures used during a speech recognition process, e.g. man-machine dialog 在语音识别过程中（例如在人机对话过程中）使用的程序
    3)[ZH]
        G09B_05/08 providing for individual presentation of information to a plurality of student stations 为多个学习（辅导）站提供各自的信息显示
        G09B_11/04 Guide sheets or plates; Tracing charts 纸张或（纸）板导引器；描图表格
        G11B_07/24038 Multiple laminated recording layers 多叠片（层积的）记录层
        A01N_65/36 Rutaceae [Rue family], e.g. lime, orange, lemon, corktree or pricklyash 芸香科，例如橙，柑（桔），柠檬，黄柏或花椒
    4)[EN]
        G01S_01/38 using comparison of (1) the phase of the envelope of the change of frequency, due to Doppler effect, of the signal transmitted by an aerial moving, or appearing to move, in a cyclic path with (2) the phase of a reference signal, the frequency of this reference signal being synchronised with that of the cyclic movement, or apparent cyclic movement, of the aerial 利用比较（1）由一个在循环路径上运动或视在运动的天线发射的信号由于多普勒效应产生的射率变化的包络的相位，以及（2）基准信号的相位，该基准信号是与循环运动或视在运动的天线的信号是同步的
    5)[EN] Plural case in ()
        G04C_23/14 Mechanisms continuously running to relate the operation(s) to the time of day 使钟表时刻与操作相联系的连续运转的机构
    6)[EN-ZH] Chemical
        A01N43/70	4	Diamino-1,3,5-triazines with only one oxygen, sulfur or halogen atom or only one cyano, thiocyano (; SCN), cyanato (OCN) or azido (N3) group directly attached to a ring carbon atom	二氨基1，3，5三嗪，仅有1个氧、硫或卤原子，或仅有1个氰基、硫氰基（—SCN），氰酰基（—OCN）或叠氮基（—N3）直接连于环碳原子上
        A01N_43/836 1,2,4-Oxa(thia)diazoles; Hydrogenated 1,2,4-oxa(thia)diazoles 1，2，4口恶（噻）二唑；氢化1，2，4口恶（噻）二唑
        A61K_31/15 Oximes (; CNO)Hydrazines (; NN)Hydrazones (; NN) 肟CON；肼NN；腙NN
        A61K_31/155 Amidines (), e.g. guanidine (H2NC(NH)NH2), isourea (HNC(OH)NH2), isothiourea (HNC(SH)NH2) 脒NCN，例如胍（H2N—C（NH）—NH2）、异脲（HNC（OH）NH2），异硫脲（NHC（SH）—NH2） 
    """

    return description


def has_cpc(description):
    """
    4. check whether a title desciption has CPC code inside
    e.g. having alternatively specified atoms bound to the phosphorus atom and not covered by a single one of groups A01N57/10, A01N57/18, A01N57/26, A01N57/34
    """
    cpc_pattern = r'[A-Za-z]{1}[0-9]{2}[A-Za-z]{0,1}[0-9]*[\/]*[0-9]*'
    match = re.search(cpc_pattern, description)
    if match:
        return True
    else:
        return False

def is_trash_title(description):
    """
    5. check whether a title description is a trash title
    """
    description = description.lower()
    
    trashZH1 = re.compile(r"在?(其他|本)[小大]?[类组]?目?的?(其他)?(各|各个)?[类组]目?中?[不未]?(适[合用]|包[含括])")
    trashZH2 = re.compile(r"在?(其他|本)[类组]目?中?[不未]?(适[合用]|包[含括])")
    trashZH3 = re.compile(r"([不未]被)?(其他|本)(单一)?[小大]?[类组]目?所?(完全)?(适[合用]|包[含括])")
    trashZH4 = re.compile(r"未(完全)?(适[合用]|包[含括])在下列各?[小大]?[类组]目?(的任何一个小组)?中?")
    trashZH5 = re.compile(r"不?(适[合用]|包[含括])?于?(其他|本)[小大]?[类组]目?中?所列")
    
    trash_de1 = re.compile(r"\t[A-Z]\w+ing\b[^的\n]+\n")
    
    if ("subject matter not" in description and "provided for in" in description) or ("covered by" in description and (" subclass " in description or " subgroup " in description or " groups " in description) and " other " in description) or ("dummy group" in description) or (description in detail_list):
        return True
    elif (re.search(trashZH1, description) or (re.search(trashZH2, description)) or (re.search(trashZH3, description)) or (re.search(trashZH4, description)) or (re.search(trashZH5, description))):
    #elif (re.search(r"在?(其他|本)[小大]?[类组]?目?的?(其他)?(各|各个)?[类组]目?中?[不未]?(包[含括])", description)):
        return True
    elif ("" in description):
        return True
    ######EN for ZH: r"\t[A-Z]\w+ing\b[^的\n]+\n"
    elif (re.search(trash_de1, description)):
        return True
    else:
        return False

def next_same_lvl_index(subdf,lvl):
    lvl_df = subdf[subdf['lvl'] == lvl]
    idx_df = lvl_df.index
    if len(idx_df) == 1:
        return idx_df[0]

    res_index = idx_df[1] - 1
    return res_index

def rm_title_with_subtree(dataframe):
    """
    6. remove those titles with codes in their description and its subtree titles
    """
    # get indices of description 
    dataframe = dataframe.reset_index(drop=True)
    id_hascpc = dataframe[dataframe['description'].apply(has_cpc) | dataframe['description'].apply(is_trash_title) | dataframe['descriptionZH'].apply(is_trash_title)].index
    print(len(id_hascpc), "removed")
    
    idx_to_drop = []
    for i in id_hascpc:
        l = dataframe.iloc[i]
        if i == (dataframe.shape[0]-1) or l['lvl'] >= dataframe.iloc[i+1]['lvl']: 
            idx_to_drop.append(i)
        else:
            j = next_same_lvl_index(dataframe[i:], l['lvl'])
            if i == j:
                idx_to_drop.append(i)
            elif j>i:
                idx_to_drop.extend(range(i,j+1))
            else:
                raise ValueError("Problem with subtree index!")

    dataframe = dataframe.drop(idx_to_drop)
    return dataframe.reset_index(drop=True)

In [7]:
def read_label_file(file_name, max_level=TARGET_LEVEL):
    df = pd.read_csv(file_name, header=None, sep='\t', dtype=object, names=['title', 'lvl', 'description', 'descriptionZH'])
    df['lvl'] = df.apply(convert_to_int, axis=1)
    print(df.shape[0], " in total")

    if max_level in [1,3,4,6]:
        df = df[df['lvl']<=dict_lvl[max_level]]

    df['description'] = df['description'].apply(clean_descr_EN)
    df['descriptionZH'] = df['descriptionZH'].apply(clean_descr_ZH)
    df = rm_title_with_subtree(df)
    return df.dropna().reset_index(drop=True)



In [8]:
def find_father(df, child_lvl):
    for i, row in df[::-1].iterrows():
        if row.lvl + 1 == child_lvl:
            return row.title

def build_tree(df, lang="ZH"):
    global node_dict
    node_dict = {}
    root_title = df.loc[0, 'title']
    if lang == "ZH":
        root_desc = df.loc[0, 'descriptionZH']
    elif lang == "EN":
        root_desc = df.loc[0, 'description']
    elif  lang == "EN-ZH":
        root_desc = df.loc[0, 'description'] + "\t" + df.loc[0, 'descriptionZH']
    print(root_desc)
    node_dict[root_title] = Node(root_desc)

    for i, row in df[1:].iterrows():
        child_lvl = row.lvl
        child_title = row.title
        if lang == "ZH":
            child_desc = row.descriptionZH
        elif lang == "EN":
            child_desc = row.description
        elif  lang == "EN-ZH":
            child_desc = row.description + "\t" + row.descriptionZH

        father_title = find_father(df[:i], child_lvl)
        try:
            node_dict[child_title] = Node(child_desc, parent = node_dict[father_title])
        except KeyError:
            print("KeyError: ", child_title, father_title, child_desc)
            print()
    return node_dict[root_title]

In [9]:
A_df = read_label_file('EN_ZH_A_cleaned_leveled.tsv')
B_df = read_label_file('EN_ZH_B_cleaned_leveled.tsv')
C_df = read_label_file('EN_ZH_C_cleaned_leveled.tsv')
D_df = read_label_file('EN_ZH_D_cleaned_leveled.tsv')
E_df = read_label_file('EN_ZH_E_cleaned_leveled.tsv')
F_df = read_label_file('EN_ZH_F_cleaned_leveled.tsv')
G_df = read_label_file('EN_ZH_G_cleaned_leveled.tsv')
H_df = read_label_file('EN_ZH_H_cleaned_leveled.tsv')

8635  in total
114 removed
15947  in total
254 removed
13864  in total
204 removed
3046  in total
61 removed
3382  in total
39 removed
8594  in total
162 removed
8088  in total
151 removed
8680  in total
186 removed


In [10]:
D_df

title  lvl                                        description  \
0            D   -3                                    TEXTILES; PAPER   
1          D01   -2    NATURAL OR MAN-MADE THREADS OR FIBRES; SPINNING   
2         D01B   -1  MECHANICAL TREATMENT OF NATURAL FIBROUS OR FIL...   
3     D01B1/00    0  Mechanical separation of fibres from plant mat...   
4     D01B1/02    1  Separating vegetable fibres from seeds, e.g. c...   
...        ...  ...                                                ...   
1791  D21J3/08    1                                         of bobbins   
1792  D21J3/10    1                                   of hollow bodies   
1793  D21J3/12    1                           of sheets; of diaphragms   
1794  D21J5/00    0  Manufacture of hollow articles by transferring...   
1795  D21J7/00    0  Manufacture of hollow articles from fibre susp...   

                         descriptionZH  
0                                纺织；造纸  
1                     天然或化学的线或纤维；纺纱或纺丝  
2     为生产纤维或长丝而对天然纤维或长丝原料进行的机械处理，如纺纱准备  
3                 从植物原料如种籽、叶、茎，机械分离出纤维  
4                         从种籽如棉籽分离植物纤维  
...                                ...  
1791                              线轴形的  
1792                             空心体形的  
1793                           平张的；板形的  
1794      用网模吸滤纤维悬浮液或纸料制成纸页再在压模中制成空心物件  
1795  利用纤维在网模中或网模上沉积的方法从纤维悬浮液或纸料制成空心物件  

[1796 rows x 4 columns]

In [197]:
print(IPC)
IPC_df = read_label_file('EN_ZH_{}_cleaned_leveled.tsv'.format(IPC))
treeENZH = build_tree(IPC_df, lang="EN-ZH")

D
49 removed
TEXTILES; PAPER	纺织；造纸


In [198]:
for pre, fill, node in RenderTree(treeENZH):
    print("%s%s" % (pre, node.name))

TEXTILES; PAPER	纺织；造纸
├── NATURAL OR MAN-MADE THREADS OR FIBRES; SPINNING	天然或化学的线或纤维；纺纱或纺丝
│   ├── MECHANICAL TREATMENT OF NATURAL FIBROUS OR FILAMENTARY MATERIAL TO OBTAIN FIBRES OR FILAMENTS, e.g. FOR SPINNING	为生产纤维或长丝而对天然纤维或长丝原料进行的机械处理，如纺纱准备
│   │   ├── Mechanical separation of fibres from plant material, e.g. seeds, leaves, stalks	从植物原料如种籽、叶、茎，机械分离出纤维
│   │   │   ├── Separating vegetable fibres from seeds, e.g. cotton	从种籽如棉籽分离植物纤维
│   │   │   │   └── Ginning	轧棉
│   │   │   │       ├── Roller gins, e.g. Macarthy type	皮辊轧棉机，如麦卡锡式
│   │   │   │       └── Saw gins	锯齿轧棉机
│   │   │   ├── Separating vegetable fibres from stalks or leaves	从茎或叶分离植物纤维
│   │   │   │   ├── Rippling	亚麻除籽或叶
│   │   │   │   ├── Breaking or scutching, e.g. of flax; Decorticating	碎麻或打麻，如亚麻的；剥制
│   │   │   │   │   ├── with devices dependent on a bending action to break or loosen fibre-bearing materials	用靠弯曲动作的装置来打开或松散含纤维的原料
│   │   │   │   │   ├── with stamping devices	用敲麻机
│   │   │   │   │   ├── with scraping devi

In [63]:
"""
（A47H_01/12，
（A61F_05/441，
（表皮郎格罕氏细胞入A61K_35/36

 
<0xa0>
"""

example = node_dict["A01B1/00"]
#print(Node("手动工具"))
#print("leaves: ", node_dict["A"].leaves)
#print("leaves: ", example.leaves)
print("is_leaf: ", example.is_leaf)
print("is_root: ", example.is_root)
print("root: ", example.root)
print("path: ", example.path)
print(example.path[0])
#print("descendants: ", example.descendants)
#print("siblings: ", example.siblings)
#print(RenderTree(example.path[-1]))
for pre, fill, node in RenderTree(example.path[-1]):
    print("%s%s" % (pre, node.name))
    
rnt = PostOrderIter(node_dict["A01B1/00"])
[node.name for node in rnt]

is_leaf:  False
is_root:  False
root:  Node('/SECTION A HUMAN NECESSITIES\t人类生活必需')
path:  (Node('/SECTION A HUMAN NECESSITIES\t人类生活必需'), Node('/SECTION A HUMAN NECESSITIES\t人类生活必需/AGRICULTURE; FORESTRY; ANIMAL HUSBANDRY; HUNTING; TRAPPING; FISHING\t农业；林业；畜牧业；狩猎；诱捕；捕鱼'), Node('/SECTION A HUMAN NECESSITIES\t人类生活必需/AGRICULTURE; FORESTRY; ANIMAL HUSBANDRY; HUNTING; TRAPPING; FISHING\t农业；林业；畜牧业；狩猎；诱捕；捕鱼/SOIL WORKING IN AGRICULTURE OR FORESTRY; PARTS, DETAILS, OR ACCESSORIES OF AGRICULTURAL MACHINES OR IMPLEMENTS, IN GENERAL\t农业或林业的整地；一般农业机械或农具的部件、零件或附件'), Node('/SECTION A HUMAN NECESSITIES\t人类生活必需/AGRICULTURE; FORESTRY; ANIMAL HUSBANDRY; HUNTING; TRAPPING; FISHING\t农业；林业；畜牧业；狩猎；诱捕；捕鱼/SOIL WORKING IN AGRICULTURE OR FORESTRY; PARTS, DETAILS, OR ACCESSORIES OF AGRICULTURAL MACHINES OR IMPLEMENTS, IN GENERAL\t农业或林业的整地；一般农业机械或农具的部件、零件或附件/Hand tools\t手动工具'))
Node('/SECTION A HUMAN NECESSITIES\t人类生活必需')
Hand tools	手动工具
├── Spades; Shovels	锹；铲
│   └── with teeth	带齿的
├── Hoes; Hand cultivators	锄；手动

In [69]:
"用于本小类所列目的的"
"本小类所列用途的"

"本大组内任何其他各组不包含的"

"(在)?本小类(的)?(其他)?(各|各个)?组(中)?不(包[含括])的"
"本小类其他组不包括的"
"本小类其他组中不包括的"
"本小类其他组不包含的"
"本小类其他组中不包含的"
"本小类其他各组中不包含的"
"本小类其他各组中不包括的"
"本小类各个组不包含的"

"(在)?其他类(目)?(中)?不(包[含括])的"
"其他类不包含的"
"其他类目不包含的"
"其他类目中不包含的"

"未被其他单一小类所完全包含的"
"未完全包含在下列各组的"
"未完全包含在下列各组的任何一个小组中的"

"不包含在其他类目中的"

"不适合于本小类其他组中所列的"

rrr = re.search(r'(在)?本小类(的)?(其他)?(各|各个)?组(中)?不(包[含括])的', "本小类其他组不包括的")
print(rrr.group())


本小类其他组不包括的


In [ ]:
"从种籽如棉籽分离植物纤维"


In [130]:
class DepParsing():

    def __init__(self):
        self.teteEN = None
        self.teteZH = None

    def parse_title(self, title):
        print(title)
        titleEN, titleZH = title.strip().split("\t")

        nlpEN = spacy.load('en_core_web_sm')
        self.docEN = nlpEN(titleEN)
        nlpZH = spacy.load('zh_core_web_sm')
        self.docZH = nlpZH(titleZH)
    
    def find_headEN(self):

        for token in self.docEN:
            #print(type(token))
            #print(token.text)
            if token.dep_ == "ROOT":
                #print(token.text)
                self.teteEN = token
                return token

    def find_headZH(self):

        for token in self.docZH:
            if token.dep_ == "ROOT":
                self.teteZH = token
                return token

    def have_same_pos(self):

        return (self.teteEN.pos_ == self.teteZH.pos_)

    def skip_hard_case(self):
        """
        to be removed with function rm_title_with_subtree()? 
        or later during parsing? -> STRICT
        """
        teteEN = self.find_headEN()
        teteZH = self.find_headZH()
        
        print("HEAD: ", teteEN,teteEN.pos_ ,teteZH,teteZH.pos_)
        
        if not (teteEN and teteZH):
            return False
        try:
            case1 = re.match(r"\t[A-Z]\w+ing\b[^的\n]+\n", teteEN.text)
            #YES(head.pos_!='NOUN'): 04N19/46	1	Embedding additional information in the video signal during the compression process	在压缩过程中在视频信号中嵌入附加信息
            #NO(head.pos_=='NOUN'): H04N5/265	3	Mixing	混合
            case2 = re.match(r"\n[^\n]+如[^；\n]+，[^或如].+\n", teteZH.text)
            #YES(): D01B1/00	0	Mechanical separation of fibres from plant material, e.g. seeds, leaves, stalks	从植物原料如种籽、叶、茎，机械分离出纤维
            #NO(): D01H1/42	2	Guards or protectors for yarns or threads, e.g. separator plates, anti-ballooning devices	纱或线的防护器，如隔纱板，气圈隔离装置
            case3 = re.search(r"[Oo]ther", teteEN.text)
            
            if case1 or case2 or case3:
                return True
            else:
                return False
        
        except AttributeError:
            return False


In [137]:
class Parser:
    """
    Basic parser for spliting cpc titles into its taxonomy structure.
    """
    def __init__(self, prepositions_file='prep_en-zh.txt', prepositionsZH_file='prep_en-zh.txt', synonym_file='synonyms.txt'):

        self.synonym_outpath = synonym_file
        self.prep_list = open(prepositions_file, 'r').read().splitlines()
        self.prepZH_list = open(prepositionsZH_file, 'r').read().splitlines()
        self.there_dict = {"thereof": "of", "therefor": "for", "therefore": "for", "therewith": "with", "therein": "in"}
        
        self.cond_replace = False
        self.cond_adj = False
        
        self.depp = DepParsing()
        
        
    def _filter_pron(self, title: str) -> bool:
        ######ZH: 代词 ==> "它们", "它们的", "其", "它的", "它"
        list_pron_EN = ["their"]
        list_pron_ZH = ["它", "其"]
        
        for pron in list_pron_EN+list_pron_ZH:
            if title.startswith(pron):
                return True
            
        title_words = title.split()
        
        if "such" in title_words:
            ######ZH: "such as" ==> "例如", "如", "诸如"
            if "such as" in title or "such a" in title:
                return False
            ######ZH: "such NOUN" ==> "这样一些", "该", "这类", "此类", "这样", "此种", "这些", "这种"
            else:
                # check whether the noun modified by "such" has already appeared in the title description
                such_noun = re.search("such (\w)*", title, re.IGNORECASE)
                if such_noun:
                    such_noun = such_noun.group(0)
                    word_after_such = such_noun.split()[-1]
                    if word_after_such in title.replace(such_noun, ""):
                        return False
                    else:
                        return True
                else:
                    return False

    def _get_syns_in_brackets(self, title: str) -> str:
        #Remove "[" "]"" from title and save synonyms (e.g. [SVM] and Support Vector Machine) 
        in_brackets = [e for e in re.finditer(r"(\[\S*\]),?;?", title)]
        if in_brackets:
            title_words = title.split(" ")
            for match in in_brackets:
                #Checking that the match is not a chemistry component: -N[O]-N= ("[" and "]" have spaces on the left/ right sides)
                if match.group() in title_words:
                    if match.group()[-1] == ";":
                        title_words[title_words.index(match.group())-1] = title_words[title_words.index(match.group())-1] + ";"
                    if match.group()[-1] == ",":
                        title_words[title_words.index(match.group())-1] = title_words[title_words.index(match.group())-1] + ","
                    title_words.remove(match.group())
                    with open(self.synonym_outpath, "a") as out_f:
                        out_f.write(match.group().strip(" ,") +"\t"+ title + "\n")
            title = " ".join(title_words)
        return title

        
    def _split(self, title: str) -> dict:
        res_forest = {}
        
        if "\t" in title:
            titleEN, titleZH = title.split("\t")
            
        # remove "reference" patterns from title
        titleEN = re.sub(r"[ ,]?(not otherwise provided for|general aspects or details|(referred to|as defined|covered) in the subgroups)[, ]?", "", titleEN, flags=re.IGNORECASE)

        # remove abbreviations inside "[" and "]"
        titleEN = self._get_syns_in_brackets(titleEN)
        titleZH = self._get_syns_in_brackets(titleZH)

        # 1. split by semicolon
        titlesEN = titleEN.split(";")
        titlesZH = titleZH.split("；")
        
        # check if EN and ZH can be aligned
        if len(titlesEN) != len(titlesZH):
            print("different ; number: ", titlesEN, titlesZH)
            return res_forest
        else:
            titles = list(zip(titlesEN, titlesZH))
            
        # [mainly for EN] remove some unuseful phrases such as "in general" or "all the like" at the end of the title
        sub_pattern = r"[ ,]?(in general|or the like|or other parts|not provided for elsewhere|specified in the subgroup)$"
        sub_patternZH = r"§§§§§§"
        
        for tuple_titles in titles:
            #print(tuple_titles)
            
            t= tuple_titles[0]
            tZH = tuple_titles[1]
            tENZH = t+"\t"+tZH
            
            t = re.sub(sub_pattern, "", t.strip(", "), flags=re.IGNORECASE).strip(", ") 
            
            # remove contents after "i.e."
            if re.search(r'i\.e\.', t):
                t = re.sub(r'[ ,]*i\.e\..*', '', t)
                tZH = re.sub(r'，?(例如|诸如|如).*', '', tZH)
                tZH = re.sub(r'[ ，]*即.*', '', tZH)
            
            # remove titles with Pronouns such as "such", "their"
            if self._filter_pron(t):
                continue
            elif  self._filter_pron(tZH):
                continue
             
            #print(t)
            #print(tZH)
            res_forest[tENZH] = Node(t+"\t"+tZH)
            #print(res_forest[tENZH].name)

        # 2. split by e.g.
            #r'，(例如|诸如|如)[：，]?'
            #A63G9/16	1	Driving mechanisms, such as ropes, gear, belt, motor drive	传动机构，例如绳索、齿轮、皮带、原动机传动装置
            eg_such = re.search(r'((e\.g\.)|(, such as))', t, flags=re.IGNORECASE)
            if eg_such:
                try:
                    eg_p, eg_c = t.split(eg_such.group())
                    eg_p = re.sub(sub_pattern, "", eg_p.strip(", "), flags=re.IGNORECASE)
                    eg_c = re.sub(sub_pattern, "", eg_c.strip(", "), flags=re.IGNORECASE)
                    
                    tZH = re.sub(r'(例如|诸如|如)[：，]?', '§§§§§§', tZH)
                    eg_pZH, eg_cZH = tZH.split('§§§§§§')
                    eg_pZH = re.sub(sub_patternZH, "", eg_pZH.strip("，"), flags=re.IGNORECASE)
                    eg_cZH = re.sub(sub_patternZH, "", eg_cZH.strip("，"), flags=re.IGNORECASE)
                    
                    res_forest[tENZH] = Node(eg_p+"\t"+eg_pZH)
                    #res_forest[t+"\t"+tZH] = Node(t+"\t"+tZH)
                    
                    # if the first word of example or the final word of main description is a preprosition, concatename them
                    try:
                        fst_word = eg_c.split()[0].lower()
                        if fst_word.lower() in eg_p[1:].lower().split(): 
                            self.cond_replace = True
                        else:
                            self.cond_replace = False
                        
                        if fst_word in self.prep_list or eg_p.split()[-1].lower() in self.prep_list: 
                            eg_c_new = self._attach_to_parent(eg_p, eg_c, fst_word, replace=self.cond_replace)
                            #eg_cZH_new = eg_pZH+"@@@"+eg_cZH
                            print("111111111111111111111111", eg_cZH, eg_pZH)
                            eg_cZH_new = self._concat_chinese(eg_cZH, eg_c, eg_pZH, eg_p, fst_word, replace=self.cond_replace)
                            print("111111111111111111111111", eg_cZH_new)
                            eg_c = eg_c_new +"\t"+ eg_cZH_new
                        else:
                            eg_c = eg_c.capitalize() +"\t"+ eg_cZH
                        res_forest[tENZH].children = [Node(eg_c)]
                        
                    except IndexError:
                         continue   # child node without content

                except ValueError: # more than one "e.g." in the title
                    """
                    A47J43/04	1	Machines for domestic use not covered elsewhere, e.g. for grinding, mixing, stirring, kneading, emulsifying, whipping or beating foodstuffs, e.g. power-driven	未列入其他类目的家用机械，如用于对食品进行研磨、混合、搅拌、揉合、乳化、搅打类的，如动力驱动的
                    """
                    eg_list = [eg.strip(", ") for eg in t.split('e.g.')]
                    eg_list = [re.sub(sub_pattern, "", eg, flags=re.IGNORECASE) for eg in eg_list]
                    eg_p = eg_list[0]
                    #print(eg_list)
                    
                    eg_listZH = [eg.strip("，") for eg in re.sub(r'(例如|诸如|如)[：，]?', '§§§§§§', tZH).split('§§§§§§')]
                    eg_pZH = eg_listZH[0]
                    #print(eg_listZH)
                    
                    # check if EN and ZH can be aligned
                    l = min(len(eg_list),len(eg_listZH))
                    if len(eg_list) != len(eg_listZH):
                        print("different e.g. number: ", eg_list, eg_listZH)
                        eg_list = eg_list[:l]
                        eg_listZH = eg_listZH[:l]
                    
                    res_forest[tENZH] = Node(eg_p +"\t"+ eg_pZH)
                    
                    if l < 2: continue
                    
                    Node_list = []                    
                    for i in range(1, len(eg_list))[::-1]:
                        eg_c = eg_list[i]
                        eg_cZH = eg_listZH[i]
                        
                        # if the first word of example or the final word of head is a preprosition, concatename their names
                        #print(eg_c,eg_cZH)
                        fst_word = eg_list[i-1].split()[0].lower()
                        if fst_word.lower() in eg_p[1:].lower().split(): 
                            self.cond_replace = True
                        else:
                            self.cond_replace = False

                        if fst_word in self.prep_list or eg_list[i-1].split()[-1].lower() in self.prep_list:
                            eg_c_new =  self._attach_to_parent(eg_list[i-1], eg_c, fst_word, replace=self.cond_replace)
                            #eg_cZH_new = eg_pZH+"@@@"+eg_cZH
                            print("222222222222222222222222", eg_cZH, eg_pZH)
                            eg_cZH_new = self._concat_chinese(eg_cZH, eg_c, eg_pZH, eg_p, fst_word, replace=self.cond_replace)
                            print("222222222222222222222222", eg_cZH_new)
                            eg_c = eg_c_new +"\t"+ eg_cZH_new
                        else:
                            eg_c = eg_c.capitalize() +"\t"+ eg_cZH  
                        #############################################
                        # WHY???
                        node_2_add = Node(eg_c)
                        try:
                            node_2_add.children = [Node_list[-1]]
                        except IndexError:
                            pass
                        Node_list.append(node_2_add)
                        #############################################
                        
                    res_forest[tENZH].children = [Node_list[-1]]
                
        return res_forest
    
    
    def _concat_chinese(self, cZH: str, cEN: str, pZH: str, pEN: str, fstw: str, for_eg: bool=True, replace=False, debug="") -> str:
        
        parent_words = list(pZH)
        newZH = ""
        """
        if cZH.endswith(pZH):
            newZH = cZH
                if for_eg:
            cond = (child_fst_word in self.prep_list) and cond
        """
        child_fst_word = cZH[0]
        
        if cZH.endswith("的"):
            newZH = cZH + pZH
        else: 
            cond_prep = (fstw in self.prep_list)
            cond_ing = fstw[0].islower() and fstw.endswith("ing")

            if replace:
                try:
                    pos = parent_words[::-1].index(child_fst_word.lower())
                    # remove tail part of parent node starts with the same preprosition
                    parent_words = parent_words[:-(pos+1)]
                except ValueError:
                    print("ValueError: ",parent_words, cZH)
                    child_node = " ".join([pZH, cZH])
                    return child_node

                child_node = " ".join(parent_words + ["的###"+cZH])

            if cond_prep:
                newZH = cZH +"的@@@"+ pZH
            elif cond_ing:
                newZH = cZH +"的&&&"+ pZH
            else:
                newZH = cZH +"的§§§"+ pZH
            
        return newZH
    
    
    def _attach_to_parent(self, parent_node: str, child_node: str, child_fst_word: str, for_eg: bool=True, replace=False, cond_adj=False) -> str:
        
        parent_words = parent_node.lower().split()
        
        if cond_adj:
            child_node = " ".join([child_node] + parent_words)
        
        else:
            ######################################################################################################
            # WHY?
            if for_eg:
                replace = (child_fst_word in self.prep_list) and replace
            ######################################################################################################
            if replace:
                try:
                    pos = parent_words[::-1].index(child_fst_word)
                    # remove tail part of parent node starts with the same preprosition
                    parent_words = parent_words[:-(pos+1)]
                except ValueError:
                    print("ValueError: ",parent_words,child_node)
                    child_node = " ".join([parent_node, child_node])
                    return child_node
                """
                D01G15/64	4	Drafting or twisting apparatus associated with doffing arrangements or with web-dividing apparatus	与道夫装置或料片分条装置联合使用的牵伸或加捻装置
                D01G15/66	5	with arrangements inserting false twist	带假捻装置
                D01G15/68	5	with arrangements inserting permanent twist, e.g. spinning	带永久加捻装置，如纺纱
                    >>>>>>
                Drafting or twisting apparatus associated with doffing arrangements or with web-dividing apparatus	与道夫装置或料片分条装置联合使用的牵伸或加捻装置
                ├── drafting or twisting apparatus associated with doffing arrangements or with arrangements inserting false twist	带假捻装置的@@@与道夫装置或料片分条装置联合使用的牵伸或加捻装置
                └── drafting or twisting apparatus associated with doffing arrangements or with arrangements inserting permanent twist	带永久加捻装置的@@@与道夫装置或料片分条装置联合使用的牵伸或加捻装置
                """
                child_node = " ".join(parent_words + [child_node])

            else:
                child_node = " ".join([parent_node, child_node])
            
        return child_node

    
    def _check(self, p_node: str, c_nodes: list) -> list:
        """
        1. check whether children nodes have the same title as parent title, if true remove the title in children nodes
        2. check whether children nodes have repeated titles among each other, if true combine their sibling nodes
        3. check if children nodes are ended with "thereof", "therefor"/"therefore" and "therewith" (without "or" also in the title), if true remove them
        """
        
        p_name = p_node.name
        c_nodes = [c for c in c_nodes if c.name != p_name]

        dict_name_siblings = defaultdict(list)  # values of dictinary are lists of Nodes
        for c in c_nodes:
            dict_name_siblings[c.name].append(c)
        
        # remove duplication children nodes
        for k,v in dict_name_siblings.items():
            head_node = v[0]
            if len(v) > 1:   
                head_children = list(copy.deepcopy(head_node.children))
                for other_node in v[1:]:
                    head_children.extend(list(copy.deepcopy(other_node.children)))
                head_node.children = head_children
            dict_name_siblings[k] = head_node
        c_nodes = list(dict_name_siblings.values())

        # titles end with therefor etc. concatenate its parent node to it (if too long just ignore and remove the last word)
        for i in range(len(c_nodes)): 
            c = c_nodes[i]
            
            cEN,cZH = c.name.strip().split("\t")[:2]    
            last_word = cEN.split()[-1].lower()
            ######################################################################################
            # Concatenation of "or parts thereof" for EN
            # ALL REMOVED FOR NOW
            """
            if last_word in self.there_dict.keys() and (not (" or parts thereof" in c.name or " OR PARTS THEREOF" in c.name)):            
                if len(words_list) < 5 and len(p_name.split()) < 5:
                    c.name = " ".join(words_list[:-1] + [self.there_dict[last_word]] + p_name.lower().split())
                else:
                    words_list = words_list[:-1]
                    c.name = " ".join(words_list)
            """
            ######################################################################################
                            
            # if the first character of children node is in lower case, then concatenate with parent node
            fst_char = c.name[0]
            self.depp.parse_title(c.name)
            teteEN = self.depp.find_headEN()
            if (teteEN.pos_!="NOUN"):
                fst_char = fst_char.lower()
            
            if fst_char.islower(): 
                
                pEN,pZH = p_name.strip().split("\t")[:2]    
                
                # c.name = " ".join([p_name,c.name])
                c_first_word = c.name.split()[0]
                if c_first_word.lower() in pEN[1:].lower().split(): 
                    self.cond_replace = True
                else:
                    self.cond_replace = False
                    
                if teteEN.pos_ == "ADJ":
                    self.cond_adj = True
                else:
                    self.cond_adj = False
                            
                cEN_new = self._attach_to_parent(pEN, cEN, c_first_word, for_eg=False, replace=self.cond_replace, cond_adj=self.cond_adj)
                #cZH_new = pZH+"@@@"+cZH
                print("333333333333333333333333", cZH, pZH)
                cZH_new = self._concat_chinese(cZH, cEN, pZH, pEN, c_first_word, replace=self.cond_replace)
                print("333333333333333333333333", cZH_new)
                c.name = cEN_new +"\t"+ cZH_new

                c_siblings = list(copy.deepcopy(c.children))
                if c_siblings:
                    for j in range(len(c_siblings)):
                        sib = copy.deepcopy(c_siblings[j])
                        #if (sib.lower())
                        if sib.name[0].islower():                                                
                            sib.parent.name = c.name
                            print(sib.name)
                            try:
                                sibEN,sibZH = sib.name.strip().split("\t")
                            except ValueError:
                                print("ValueError: ", c.name, sib.name)
                                continue
                            sib_first_word = sib.name.split()[0]
                            if sib_first_word.lower() in cEN_new[1:].lower().split(): 
                                self.cond_replace = True
                            else:
                                self.cond_replace = False
                            # sib.name = " ".join([p_name, sib.name])
                            ######################################################################################
                            # Why "p_name" here, shounldn't be "cEN_new" ?
                            #sib.name = self._attach_to_parent(p_name, sib.name, sib.name.split()[0], for_eg= False)
                            sibEN_new = self._attach_to_parent(cEN_new, sibEN, sib_first_word, for_eg=False, replace=self.cond_replace)
                            #sibZH_new = cZH_new+"@@@"+sibZH
                            print("444444444444444444444444", sibZH, cZH)
                            sibZH_new = self._concat_chinese(sibZH, sibEN, cZH_new, cEN_new, sib_first_word, replace=self.cond_replace)
                            print("444444444444444444444444", sibZH_new)
                            sib.name = sibEN_new +"\t"+ sibZH
                            ######################################################################################
                            
                            c_siblings[j] = sib
                    
                    c.childern = [] #TODO zy: no idea why it works :)
                    c.children = c_siblings
            
            c_nodes[i] = c
            
        return c_nodes
    
    
    def _valide(self, root_node: str) -> Node:
        # all nodes in pre order 
        nodes_to_search = [node for node in PreOrderIter(root_node)][1:]
        for node in nodes_to_search:
            # check if node starts with lower case
            fst_word = node.name.split()[0]
            
            #############################################################################################
            # remove "other than .*" at the end of title
            node.name = re.sub(r"other than .*", "", node.name, flags=re.IGNORECASE).strip(", ")
            #############################################################################################
            
            if (node.name[0].islower() and fst_word in node.parent.name and fst_word != node.parent.name.lower().split()[0]):
                try:
                    nameEN,nameZH = node.name.strip().split("\t")
                    parentEN,parentZH = node.parent.name.strip().split("\t")
                except ValueError:
                    print("ValueError: ", node.name, node.parent.name)
                    continue
                
                if fst_word.lower() in parentEN[1:].lower().split(): 
                    self.cond_replace = True
                else:
                    self.cond_replace = False
                    
                nameEN_new = self._attach_to_parent(parentEN, nameEN, fst_word, for_eg=False, replace=self.cond_replace)
                #nameZH_new = parentZH+"@@@"+nameZH
                print("555555555555555555555555", nameZH, parentZH)
                nameZH_new = self._concat_chinese(nameZH, nameEN, parentZH, parentEN, fst_word, replace=self.cond_replace)
                print("555555555555555555555555", nameZH_new)
                node.name = nameEN_new +"\t"+ nameZH_new
            
            """
            # check if there is "such as" in the title
            if (" such as " in node.name.lower()):
                sa_p, sa_c = re.split(" such as | SUCH AS ", node.name, 1)
                sa_p =  sa_p.strip(", ")
                sa_c =  sa_c.strip(", ")
                node.name = sa_p
                node.children = list(copy.deepcopy(node.children)) + [Node(sa_c)]    

            # check if node starts with "Details"
            if node.name[:7].lower() == "details":
                try:
                    if node.children:
                        node.parent.children = node.children
                        for c_node in node.children:
                            c_node.parent = node.parent
                    else:
                        node.parent.children = []
                except:
                    print("error with it: ", node) #TODO
            """
                
        return root_node
    

    def _update_child_layer(self, p_node: Node, c_nodes: list, clean_p: bool) -> Node:
        """
        concatenate a parent node and its children nodes (childnode could be a tree depends on the results of splitting)
        """
        if clean_p:
            children_list = []
        else:
            children_list = list(p_node.children)   # original children nodes of the parent node
        for c in c_nodes:
            # check if vide name, if yes delete it
            if not c.name:
                c_nodes.remove(c)
        
        children_list.extend(c_nodes)                   
        p_node.children = children_list
        
        return p_node

    
    def get_taxonomy(self, root_node, root_name: str, valide=True, strict=True) -> Node:
        # create new root node 
        res_root = Node(root_name)

        # all nodes in post order 
        nodes_to_search = [node for node in PostOrderIter(root_node)]
        #print(nodes_to_search[-1].name)
        last_node = nodes_to_search[-1].name
        
        saved_nodes = defaultdict(str)
        top_layer = []
        
        print("************************************************************************************************************")
        print(f"Creating taxonomy tree for {root_name} ")
        print("************************************************************************************************************")
                
        for node in tqdm(nodes_to_search):
            last = (node.name==last_node)
            print("\nCURRANT NODE: ", node.name)
            print(last)
            
            c_layer = list(self._split(node.name).values()) # returns a list of Nodes after splitting
            
            # preprocessing for titles with "therefor" "thereof" etc.
            nodes_to_remove = []
            for i in range(len(c_layer)):
                c = c_layer[i]
                
                #print(c.name)
                #print(c.name.strip().split("\t"))
                EN_ZH = c.name.strip().split("\t")
                if len(EN_ZH) != 2:
                    print("UNCORRECT TITLE: ", EN_ZH)
                    nodes_to_remove.append(c)
                    continue
                else:
                    EN,ZH = EN_ZH
                    
                # remove titles only containing the word "Details"
                if (EN in detail_list): 
                    nodes_to_remove.append(c)
                    continue
                
                if strict:
                    self.depp.parse_title(c.name)
                    if self.depp.skip_hard_case():
                        nodes_to_remove.append(c)
                        continue

                words_list = EN.split()
                words_listZH = ZH.split()    
                try:      
                    last_word = words_list[-1].lower()
                except IndexError:
                    nodes_to_remove.append(c)
                    continue
                #################################################################################################
                # Concatenation of "or parts thereof" for EN
                # ALL REMOVED FOR NOW
                if last_word in self.there_dict.keys() and (not (" or parts thereof" in c.name or " OR PARTS THEREOF" in c.name)):
                    """
                    if len(c_layer) > 1:
                        # concatenate the content of current node with its previous brother node if possible
                        brother_name,brother_nameZH = c_layer[i-1].name.strip().split("\t")
                        
                        if brother_name:
                            brother_lasw = brother_name.split()[-1].lower()

                            if len(words_list) < 5 and len(brother_name.split()) < 5 and not (brother_lasw in self.there_dict.keys()):
                                EN_concat = " ".join(words_list[:-1] + [self.there_dict[last_word]] + brother_name.lower().split())
                                ZH_concat = 
                                c.name = EN_concat +"\t"+ ZH_concat
                                c_layer[i] = c 
                            else:
                                nodes_to_remove.append(c)
                    """
                    nodes_to_remove.append(c)
                #################################################################################################
                                
            c_layer = [c for c in c_layer if not (c in nodes_to_remove)]
            #print("c_layer: ({})".format(len(c_layer)), c_layer)
                
            # if current node has children nodes already updated
            if node.name + str(node.depth) in saved_nodes:
                siblings = saved_nodes[node.name + str(node.depth)] # a list of children nodes of current node
                for c in c_layer:
                    #c.children = self._valide(c, copy.deepcopy(c.children)+copy.deepcopy(siblings.children))
                    c.children = self._check(c, copy.deepcopy(c.children)+copy.deepcopy(siblings.children))
                    #print(c.children)
                    
            p_node = copy.deepcopy(node.parent)
            #print(node.is_root)
            if last:
                print("************************************************************************************************************")
                top_layer.extend(c_layer)
            elif p_node:
                if p_node.name + str(p_node.depth) in saved_nodes:
                    new_p = False  
                    p_node = saved_nodes[p_node.name + str(p_node.depth)]
                else:
                    new_p = True
                p_v = self._update_child_layer(p_node, c_layer, clean_p=new_p)

                # update parent node in result dictionary
                saved_nodes[p_node.name+str(p_node.depth)] = p_v
                
        print("top_layer : ", top_layer)
        res_root.children = copy.deepcopy(top_layer)
        res_root.name = "SECTION {} - ".format(IPC) + res_root.name
        
        if valide:
            # to check the title connatenation from root node to leaf nodes
            res_root = self._valide(res_root)
        
        print("************************************************************************************************************")
        
        return res_root

In [ ]:
IPC = "D"
STRICT = True
VALIDE = True
LEVEL = 6

#print(IPC)
IPC_df = read_label_file('EN_ZH_{}_cleaned_leveled.tsv'.format(IPC), LEVEL)
treeENZH = build_tree(IPC_df, lang="EN-ZH")

root_test = IPC # "A63H" "A01N63/00"
node_test = node_dict[root_test]
title_test = node_dict[root_test].name
print(title_test)

parse = Parser()
concat_node_test = parse.get_taxonomy(node_test, title_test, VALIDE, STRICT)


3046  in total
41 removed
TEXTILES; PAPER	纺织；造纸
TEXTILES; PAPER	纺织；造纸
************************************************************************************************************
Creating taxonomy tree for TEXTILES; PAPER	纺织；造纸 
************************************************************************************************************


  0%|                                                                       | 0/241 [00:00<?, ?it/s]


CURRANT NODE:  Mechanical separation of fibres from plant material, e.g. seeds, leaves, stalks	从植物原料如种籽、叶、茎，机械分离出纤维
False
Mechanical separation of fibres from plant material	从植物原料


  0%|▎                                                              | 1/241 [00:02<09:57,  2.49s/it]

HEAD:  separation NOUN 原料 NOUN

CURRANT NODE:  Mechanical removal of impurities from animal fibres	动物纤维机械除杂
False
Mechanical removal of impurities from animal fibres	动物纤维机械除杂


...

HEAD:  Casings NOUN 缝纫机 PROPN

CURRANT NODE:  Frames, stands, tables, or other furniture adapted to carry sewing machines	用来装载缝纫机的支架、台板或其他家具
False
Frames, stands, tables, or other furniture adapted to carry sewing machines	用来装载缝纫机的支架、台板或其他家具


 74%|█████████████████████████████████████████████▎               | 179/241 [11:44<01:22,  1.33s/it]

HEAD:  stands NOUN 用来 VERB

CURRANT NODE:  Covers, or portable enclosures, for sewing machines	缝纫机罩或手提式罩壳
False
Covers, or portable enclosures, for sewing machines	缝纫机罩或手提式罩壳


 75%|█████████████████████████████████████████████▌               | 180/241 [11:45<01:20,  1.32s/it]

HEAD:  Covers NOUN 罩壳 NOUN

CURRANT NODE:  Incorporations or adaptations of lighting equipment for sewing machines	缝纫机照明设备的结合或改装
False
Incorporations or adaptations of lighting equipment for sewing machines	缝纫机照明设备的结合或改装


In [124]:
with open("tree_ipc/{}_tree_ipc{}.txt".format(IPC, str(LEVEL)), "w") as o:
    for pre, fill, node in RenderTree(concat_node_test):
        print("%s%s" % (pre, node.name))
        o.write("%s%s\n" % (pre, node.name))

SECTION D - TEXTILES; PAPER	纺织；造纸
├── TEXTILES	纺织
│   ├── TEXTILES NATURAL OR MAN-MADE THREADS OR FIBRES	天然或化学的线或纤维的§§§纺织
│   │   ├── NATURAL OR MAN-MADE THREADS OR FIBRES MECHANICAL TREATMENT OF NATURAL FIBROUS OR FILAMENTARY MATERIAL TO OBTAIN FIBRES OR FILAMENTS	为生产纤维或长丝而对天然纤维或长丝原料进行的机械处理的§§§天然或化学的线或纤维
│   │   │   ├── MECHANICAL TREATMENT OF NATURAL FIBROUS OR FILAMENTARY MATERIAL TO OBTAIN FIBRES OR FILAMENTS For spinning	纺纱准备的§§§为生产纤维或长丝而对天然纤维或长丝原料进行的机械处理
│   │   │   ├── Mechanical separation of fibres from plant material	从植物原料
│   │   │   │   └── Seeds, leaves, stalks	种籽、叶、茎，机械分离出纤维
│   │   │   ├── Mechanical removal of impurities from animal fibres	动物纤维机械除杂
│   │   │   ├── Hackling or heckling machines	栉梳或栉梳机
│   │   │   ├── MECHANICAL TREATMENT OF NATURAL FIBROUS OR FILAMENTARY MATERIAL TO OBTAIN FIBRES OR FILAMENTS Obtaining silk fibres or filaments	丝纤维或长丝的生产的§§§为生产纤维或长丝而对天然纤维或长丝原料进行的机械处理
│   │   │   └── Other mechanical treatment of natural fibrous or filamentary material to 

In [68]:
# save term-hyponym pairs into csv file
with open("/pairs/hH_ipc{}_{}.csv".format(str(LEVEL), IPC), "w", newline='') as csv_f:
    writer = csv.writer(csv_f, delimiter=",", quoting=csv.QUOTE_MINIMAL)
    nodes = [node for node in PreOrderIter(concat_node_test)]
    for node in nodes[2:]:
        writer.writerow([node.name, node.parent.name])
        #writer.writerow([node.name.lower(), node.parent.name.lower()])
        
# remove duplicates hyper/hypo pairs
df = pd.read_csv("/pairs/hH_ipc{}_{}.csv".format(str(LEVEL), IPC), header=None, sep=',', dtype=object, names=["hyponym","hyperonym"])
print(df.shape)
df_unique = df.drop_duplicates()
print(df_unique.shape)

_, manual_eval = train_test_split(df, test_size=500, random_state=100)
#train=df_unique.sample(frac=0.8,random_state=200)
print(manual_eval.shape)
#manual_eval

manual_eval.to_csv("/pairs/hH_random_ipc{}_{}500.csv".format(str(LEVEL), IPC), index=False)

(56564, 2)
(10350, 2)
(500, 2)


3046  in total
51 removed
TEXTILES; PAPER	纺织；造纸
TEXTILES; PAPER	纺织；造纸
************************************************************************************************************
Creating taxonomy tree for TEXTILES; PAPER	纺织；造纸 ...
************************************************************************************************************


  0%|▏                                                             | 4/1796 [00:00<00:49, 36.45it/s]


CURRANT NODE:  Roller gins, e.g. Macarthy type	皮辊轧棉机，如麦卡锡式
False

CURRANT NODE:  Saw gins	锯齿轧棉机
False

CURRANT NODE:  Ginning	轧棉
False

CURRANT NODE:  Separating vegetable fibres from seeds, e.g. cotton	从种籽如棉籽分离植物纤维
False

CURRANT NODE:  Rippling	亚麻除籽或叶
False

CURRANT NODE:  with devices dependent on a bending action to break or loosen fibre-bearing materials	用靠弯曲动作的装置来打开或松散含纤维的原料
False

CURRANT NODE:  with stamping devices	用敲麻机
False

CURRANT NODE:  with scraping devices	用刮麻装置
False

CURRANT NODE:  with crushing or breaking rollers or plates	用压碎辊或板
False

CURRANT NODE:  with toothed or other pointed devices	用锯齿状或其他尖形装置
False


  1%|▎                                                            | 11/1796 [00:00<00:33, 53.19it/s]


CURRANT NODE:  with beaters rotating about an axis parallel to the fibre bundle	用沿着与纤维束相平行的轴线旋转的打麻机
False

CURRANT NODE:  with beaters rotating about an axis perpendicular to the fibre bundle	用沿着与纤维束相垂直的轴线旋转的打麻机
False

CURRANT NODE:  Feeding arrangements	喂入装置
False

CURRANT NODE:  Conveying devices, e.g. moving bands or ropes	传送装置，如运输带或绳
False

CURRANT NODE:  Devices holding fibres or fibre-bearing materials during treatment	在处理过程中容纳纤维或支撑纤维原料的装置
False

CURRANT NODE:  Delivery or discharge arrangements	输出或卸料装置
False


...

100%|██████████████████████████████████████████████████████████▉| 1795/1796 [01:20<00:00, 41.27it/s]


CURRANT NODE:  of hollow bodies	空心体形的
False

CURRANT NODE:  of sheets; of diaphragms	平张的；板形的
False

CURRANT NODE:  Manufacture of articles by pressing wet fibre pulp, or papier-mâché, between moulds	在模型中压榨纤维纸浆或纸料制造物件
False
333333333333333333333333 环形的 在模型中压榨纤维纸浆或纸料制造物件
333333333333333333333333 环形的在模型中压榨纤维纸浆或纸料制造物件
333333333333333333333333 管形的 在模型中压榨纤维纸浆或纸料制造物件
333333333333333333333333 管形的在模型中压榨纤维纸浆或纸料制造物件
333333333333333333333333 塞形的 在模型中压榨纤维纸浆或纸料制造物件
333333333333333333333333 塞形的在模型中压榨纤维纸浆或纸料制造物件
333333333333333333333333 线轴形的 在模型中压榨纤维纸浆或纸料制造物件
333333333333333333333333 线轴形的在模型中压榨纤维纸浆或纸料制造物件
333333333333333333333333 空心体形的 在模型中压榨纤维纸浆或纸料制造物件
333333333333333333333333 空心体形的在模型中压榨纤维纸浆或纸料制造物件
333333333333333333333333 平张的 在模型中压榨纤维纸浆或纸料制造物件
333333333333333333333333 平张的在模型中压榨纤维纸浆或纸料制造物件
333333333333333333333333 板形的 在模型中压榨纤维纸浆或纸料制造物件
333333333333333333333333 板形的在模型中压榨纤维纸浆或纸料制造物件

CURRANT NODE:  Manufacture of hollow articles by transferring sheets, produced from fibres suspensions or papier-mâché

100%|███████████████████████████████████████████████████████████| 1796/1796 [01:21<00:00, 22.15it/s]


************************************************************************************************************
top_layer :  [Node('/TEXTILES\t纺织'), Node('/PAPER\t造纸')]
ValueError:  from organic cellulose esters or ethers by the dry spinning process	干法的§§§有机纤维素酯或醚
ValueError:  from polypropylene	用聚丙烯的§§§用聚烯烃
ValueError:  from polyvinyl chloride or polyvinylidene chloride	用聚氯乙烯或聚偏二氯乙烯的§§§用卤代烃聚合物
ValueError:  from polymers of fluorinated hydrocarbons	用氟代烃聚合物的§§§用卤代烃聚合物
ValueError:  from polystyrene	用聚苯乙烯的§§§用侧链中含一个碳—碳双键的环状聚合物
ValueError:  from polycarbonates	用聚碳酸酯的§§§用聚酯
ValueError:  by decomposition of organic filaments	通过有机长丝的分解 from coal pitch	从煤沥青的§§§从沥青或蒸馏残余物
ValueError:  by decomposition of organic filaments	通过有机长丝的分解 from petroleum pitch	从石油沥青的§§§从沥青或蒸馏残余物
ValueError:  by decomposition of organic filaments	通过有机长丝的分解 from macromolecular compounds obtained by reactions only involving carbon-to-carbon unsaturated bonds	仅包括碳—碳不饱和键反应得到的高分子化合物的§§§从加聚、缩聚或聚合产物
ValueError:  from polyacrylonit

ValueError:  by needling or like operations to cause entanglement of fibres	通过针刺或类似的方法使纤维相互缠结在一起 in combination with weld-bonding	与熔焊相结合的@@@至少结合采用一种其他方法进行压实
ValueError:  by needling or like operations to cause entanglement of fibres	通过针刺或类似的方法使纤维相互缠结在一起 in combination with bonding agents	与黏合剂相结合的@@@至少结合采用一种其他方法进行压实
ValueError:  by needling or like operations to cause entanglement of fibres	通过针刺或类似的方法使纤维相互缠结在一起 in combination with at least one other method of consolidation entanglement by fluid jet in combination with another consolidation means	通过流体喷射与另一压实装置相结合而缠结的§§§至少结合采用一种其他方法进行压实
ValueError:  the fleeces or layers being consolidated by fluid jet	通过流体喷射的§§§通过针刺或类似的方法使纤维相互缠结在一起
555555555555555555555555 用于形成图案的§§§通过流体喷射 通过流体喷射的§§§通过针刺或类似的方法使纤维相互缠结在一起
555555555555555555555555 用于形成图案的§§§通过流体喷射的§§§通过流体喷射的§§§通过针刺或类似的方法使纤维相互缠结在一起
ValueError:  the fleeces or layers being consolidated by needling or like operations to cause entanglement of layered webs	多层网的缠结的§§§通过针刺或类似的方法使纤维相互缠结在一起
ValueErr

In [ ]:
"""
ValueError:  ['fibreboard'] Fibreboard
333333333333333333333333 纤维板 纤维板
ValueError:  ['纤维板'] 纤维板
333333333333333333333333 纤维板 纤维板


ValueError:  ['spinning'] SPINNING OR TWISTING
333333333333333333333333 纺纱或加捻 纺纱或纺丝
ValueError:  ['纺纱或纺丝'] 纺纱或加捻
333333333333333333333333 纺纱或纺丝 纺纱或加捻


Roller gins	皮辊轧棉机
└── Macarthy type	麦卡锡式


carbon filaments by decomposition of organic filaments from proteins	从蛋白质的§§§通过有机长丝的分解
└── From wool	羊毛


├── Conjugated	共轭的
D01F8/00	0	Conjugated, i.e. bi- or multicomponent, man-made filaments or the like; Manufacture thereof	共轭的，即二组分或多组分人造长丝或类似物；其制造


蒸气是冷的 利用特殊蒸气


该装置是在活塞内的一个密封室中使用液体或固体冷却剂的具有冷却装置
该装置是流体通过或沿着活塞流动的§§§具有冷却装置
用于协助最终关闭或用于初始开启的@@@以动力致动器的功能或用途为特征


Details	零件
G02C11/00	0	Non-optical adjuncts; Attachment thereof	非光学附件；其连接


G01C19/5733	3	Structural details or topology	结构细节或拓扑
G01C19/574	4	the devices having two sensing masses in anti-phase motion	反相运动中具有两个传感部件的装置

D05B3/12	1	for fastening articles by sewing	缝制扣紧件的
D05B3/14	2	perforated or press buttons	穿孔扣或按扣
D05B3/16	2	shank buttons	有脚纽扣
D05B3/18	2	hooks or eyelets	挂钩或纽孔
D05B3/20	2	labels	标签

D05C1/04	2	circular	圆弓

D06B1/10	1	by contact with a member carrying the treating material	与纺织材料传送装置相接触
D06B1/12	2	by rubbing contact, e.g. with brushes or pads	摩擦接触，如与刷子或衬垫
D06B1/14	2	with a roller	与滚筒

D06B5/12	1	through materials of definite length	透过一定长度的纺织材料
D06B5/14	2	through fibres, slivers, or rovings	透过纤维、棉条或粗纱
D06B5/16	2	through yarns, threads, or filaments	透过纱、线和长丝
D06B5/18	3	through beamed warp	透过轴经纱
D06B5/20	3	through hanks	透过绞纱
D06B5/22	2	through fabrics	透过织物
D06B5/24	2	through articles, e.g. stockings	透过成品，如长袜
D06B5/26	2	using centrifugal force	运用离心力

D06C9/00	0	Singeing	烧毛
D06C9/02	1	by flame	火焰

D06F21/00	0	Washing machines with receptacles, e.g. perforated, having a rotary movement, e.g. oscillatory movement	带容器的洗衣机，如带孔的、能旋转或振动的容器
D06F21/02	1	about a horizontal axis	沿横轴线的
D06F21/04	2	within an enclosing receptacle	在封闭式容器内

D01G15/64	4	Drafting or twisting apparatus associated with doffing arrangements or with web-dividing apparatus	与道夫装置或料片分条装置联合使用的牵伸或加捻装置
D01G15/66	5	with arrangements inserting false twist	带假捻装置
D01G15/68	5	with arrangements inserting permanent twist, e.g. spinning	带永久加捻装置，如纺纱
Drafting or twisting apparatus associated with doffing arrangements or with web-dividing apparatus	与道夫装置或料片分条装置联合使用的牵伸或加捻装置
├── drafting or twisting apparatus associated with doffing arrangements or with arrangements inserting false twist	带假捻装置的@@@与道夫装置或料片分条装置联合使用的牵伸或加捻装置
└── drafting or twisting apparatus associated with doffing arrangements or with arrangements inserting permanent twist	带永久加捻装置的@@@与道夫装置或料片分条装置联合使用的牵伸或加捻装置

"""

        """
        A23L2/42	1	Preservation of non-alcoholic beverages	非酒精饮料的保藏
        A23L2/44	2	by adding preservatives	加防腐剂
        A23L2/46	2	by heating	加热
        A23L2/48	3	by irradiation or electric treatment	辐射或电处理
        A23L2/50	2	by irradiation or electric treatment without heating	辐射或电处理但不加热
        
        A23L2/00	0	Non-alcoholic beverages; Dry compositions or concentrates therefor; Their preparation	非酒精饮料；其干组合物或浓缩物；它们的制备
        A23L2/52	1	Adding ingredients	加入组分
        A23L2/54	2	Mixing with gases	与气体混合
        
        A23K30/00	0	Processes specially adapted for preservation of materials in order to produce animal feeding-stuffs	专门适用于生产动物饲料原料的保存方法
        A23K30/10	1	of green fodder	青饲料的
        A23K30/12	2	Dehydration	青饲料脱水
        A23K30/15	2	using chemicals or micro-organisms for ensilaging	使用化学物质或微生物青贮饲料
        A23K30/18	3	using micro-organisms or enzymes	用微生物或酶青贮
        """


"Ploughs supported partly by tractor and partly by their own wheels	半悬挂犁，即一部分由拖拉机支持，另一部分由自身轮支撑"

"Exercising apparatus combining several parts such as ladders, rods, beams, slides rigidly combined	组合几种部件，例如梯、杆、横木、滑板的锻炼器械@@@刚性结合的"
"Exercising apparatus combining several parts such as ladders, rods, beams, slides separable	组合几种部件，例如梯、杆、横木、滑板的锻炼器械@@@可拆式的"

"exercising apparatus for developing or strengthening the muscles or joints of the body by working against a counterforce, with or without measuring devices using frictional force-resisters including rotating or oscillating elements	带有或不带有测量装置，不依靠推力而促进或增强人体的肌肉或关节生长的训练器械@@@使用摩擦阻力装置@@@使用摩擦阻力装置@@@包括转动或摆动元件"
"exercising apparatus for developing or strengthening the muscles or joints of the body by working against a counterforce, with or without measuring devices using frictional force-resisters including a rope moving relative to the surface of elements	带有或不带有测量装置，不依靠推力而促进或增强人体的肌肉或关节生长的训练器械@@@使用摩擦阻力装置@@@使用摩擦阻力装置@@@包括相对于元件表面运动的绳索"

"Exercising apparatus for developing or strengthening the muscles or joints of the body by working against a counterforce, with or without measuring devices using resilient force-resisters	带有或不带有测量装置，不依靠推力而促进或增强人体的肌肉或关节生长的训练器械@@@使用弹性阻力装置"
    "exercising apparatus for developing or strengthening the muscles or joints of the body by working against a counterforce, with or without measuring devices using resilient force-resisters attached to static foundation	带有或不带有测量装置，不依靠推力而促进或增强人体的肌肉或关节生长的训练器械@@@使用弹性阻力装置@@@使用弹性阻力装置@@@附加于固定的基础"
    "exercising apparatus for developing or strengthening the muscles or joints of the body by working against a counterforce, with or without measuring devices using resilient force-resisters having torsion element	带有或不带有测量装置，不依靠推力而促进或增强人体的肌肉或关节生长的训练器械@@@使用弹性阻力装置@@@使用弹性阻力装置@@@具有扭转元件"

Creating taxonomy tree for MECHANICAL ENGINEERING; LIGHTING; HEATING; WEAPONS; BLASTING	机械工程；照明；加热；武器；爆破 ...


  0%|                                                              | 1/7756 [00:00<17:17,  7.47it/s]


CURRANT NODE:  with one single cylinder	带有单个汽缸
False

CURRANT NODE:  with cylinders all in one line	带有单排汽缸
False

CURRANT NODE:  with cylinders in V-arrangement	带有Ⅴ形汽缸排列的
False


  0%|                                                              | 3/7756 [00:00<12:43, 10.16it/s]


CURRANT NODE:  with cylinders in star or fan arrangement	带有星形或扇形排列汽缸的
False

CURRANT NODE:  with cylinders arranged oppositely relative to main shaft and of "flat" type	带有相对主轴对置排列且处于一个平面上的汽缸
False


...

555555555555555555555555 活塞连接是在缸的外端的§§§缸垂直于传动装置的主轴线配置 缸垂直于传动装置的主轴线配置的@@@各有1个主轴并备有在缸内作往复运动的活塞的§§§各有1个主轴并备有在缸内作往复运动的活塞的§§§泵和马达属同一类型的@@@泵和马达属同一类型的§§§带有组合成一体的液压马达和液压泵
555555555555555555555555 活塞连接是在缸的外端的§§§缸垂直于传动装置的主轴线配置的§§§缸垂直于传动装置的主轴线配置的@@@各有1个主轴并备有在缸内作往复运动的活塞的§§§各有1个主轴并备有在缸内作往复运动的活塞的§§§泵和马达属同一类型的@@@泵和马达属同一类型的§§§带有组合成一体的液压马达和液压泵
555555555555555555555555 活塞连接是在缸的内端的§§§缸垂直于传动装置的主轴线配置 缸垂直于传动装置的主轴线配置的@@@各有1个主轴并备有在缸内作往复运动的活塞的§§§各有1个主轴并备有在缸内作往复运动的活塞的§§§泵和马达属同一类型的@@@泵和马达属同一类型的§§§带有组合成一体的液压马达和液压泵
555555555555555555555555 活塞连接是在缸的内端的§§§缸垂直于传动装置的主轴线配置的§§§缸垂直于传动装置的主轴线配置的@@@各有1个主轴并备有在缸内作往复运动的活塞的§§§各有1个主轴并备有在缸内作往复运动的活塞的§§§泵和马达属同一类型的@@@泵和马达属同一类型的§§§带有组合成一体的液压马达和液压泵
555555555555555555555555 液室成形为与传动装置主轴线同心的旋转体的@@@泵和马达属同一类型 泵和马达属同一类型的§§§带有组合成一体的液压马达和液压泵
555555555555555555555555 液室成形为与传动装置主轴线同心的旋转体的@@@泵和马达属同一类型的@@@泵和马达属同一类型的§§§带有组合成一体的液压马达和液压泵
555555555555555555555555 带有旋转位移元件的@@@液室成形为与传动装置主轴线同心的旋转体 液室成形为与传动装置主轴线同心的旋转体的@@@泵和马达属同一类型的@@@泵和马达属同一类型的§§§带有组合成一体的液压马达和液压泵
555555555555555555555555 带有旋转位移元件的@@@液室成

555555555555555555555555 流体作用在隔膜上的§§§安装在手动阀上或与手动阀组合的§§§安装在手动阀上或与手动阀组合的@@@由流体致动
555555555555555555555555 流体作用在活塞上的§§§在液力马达和闭合元件之间带有一个不同于推杆或拉杆的机构 在液力马达和闭合元件之间带有一个不同于推杆或拉杆的机构的@@@由流体致动
555555555555555555555555 流体作用在活塞上的§§§在液力马达和闭合元件之间带有一个不同于推杆或拉杆的机构的§§§在液力马达和闭合元件之间带有一个不同于推杆或拉杆的机构的@@@由流体致动
555555555555555555555555 流体作用在隔膜上的§§§在液力马达和闭合元件之间带有一个不同于推杆或拉杆的机构 在液力马达和闭合元件之间带有一个不同于推杆或拉杆的机构的@@@由流体致动
555555555555555555555555 流体作用在隔膜上的§§§在液力马达和闭合元件之间带有一个不同于推杆或拉杆的机构的§§§在液力马达和闭合元件之间带有一个不同于推杆或拉杆的机构的@@@由流体致动
555555555555555555555555 致动提升阀的&&&由浮子致动 由浮子致动的§§§由流体致动
555555555555555555555555 致动提升阀的&&&由浮子致动的§§§由浮子致动的§§§由流体致动
555555555555555555555555 浮子与阀刚性连接的@@@致动提升阀 致动提升阀的&&&由浮子致动的§§§由浮子致动的§§§由流体致动
555555555555555555555555 浮子与阀刚性连接的@@@致动提升阀的§§§致动提升阀的&&&由浮子致动的§§§由浮子致动的§§§由流体致动
555555555555555555555555 带有其零件从单浮子至单阀连接在一起的传动装置的@@@致动提升阀 致动提升阀的&&&由浮子致动的§§§由浮子致动的§§§由流体致动
555555555555555555555555 带有其零件从单浮子至单阀连接在一起的传动装置的@@@致动提升阀的§§§致动提升阀的&&&由浮子致动的§§§由浮子致动的§§§由流体致动
555555555555555555555555 带有作直线运动的引导阀和与铰臂连接的浮子的@@@带有其零件从单

555555555555555555555555 从一个吊架上悬挂的分离的分离的紧固地围绕着管子、电缆或护管的
555555555555555555555555 沿着约束表面延伸的包含一个牢固地环绕管子、电缆或护管的元件 包含一个牢固地环绕管子、电缆或护管的元件的&&&紧固地围绕着管子、电缆或护管的
555555555555555555555555 沿着约束表面延伸的包含一个牢固地环绕管子、电缆或护管的元件的§§§包含一个牢固地环绕管子、电缆或护管的元件的&&&紧固地围绕着管子、电缆或护管的
555555555555555555555555 从约束表面延伸的包含一个牢固地环绕管子、电缆或护管的元件 包含一个牢固地环绕管子、电缆或护管的元件的&&&紧固地围绕着管子、电缆或护管的
555555555555555555555555 从约束表面延伸的包含一个牢固地环绕管子、电缆或护管的元件的§§§包含一个牢固地环绕管子、电缆或护管的元件的&&&紧固地围绕着管子、电缆或护管的
555555555555555555555555 通过快速作用约束的包含一个牢固地环绕管子、电缆或护管的元件 包含一个牢固地环绕管子、电缆或护管的元件的&&&紧固地围绕着管子、电缆或护管的
555555555555555555555555 通过快速作用约束的包含一个牢固地环绕管子、电缆或护管的元件的§§§包含一个牢固地环绕管子、电缆或护管的元件的&&&紧固地围绕着管子、电缆或护管的
555555555555555555555555 从一个吊架悬挂的包含一个牢固地环绕管子、电缆或护管的元件 包含一个牢固地环绕管子、电缆或护管的元件的&&&紧固地围绕着管子、电缆或护管的
555555555555555555555555 从一个吊架悬挂的包含一个牢固地环绕管子、电缆或护管的元件的§§§包含一个牢固地环绕管子、电缆或护管的元件的&&&紧固地围绕着管子、电缆或护管的
555555555555555555555555 由挠性带组成的包含一个牢固地环绕管子、电缆或护管的元件 包含一个牢固地环绕管子、电缆或护管的元件的&&&紧固地围绕着管子、电缆或护管的
555555555555555555555555 由挠性带组成的包含一个牢固地环绕管子、电缆或护管的元件的§§§包含一个牢固地环绕管子、电缆或护管的元件的&&&紧固地

555555555555555555555555 带滚柱或往复炉条的带有可移动且基本保持同样位置的燃料推进元件的燃料支撑面的@@@带有可移动且基本保持同样位置的燃料推进元件的燃料支撑面的@@@带有专门适用于通过燃烧区推进燃料的燃料支撑面的带有专门适用于通过燃烧区推进燃料的燃料支撑面的具有可移动组件的燃料支撑面
555555555555555555555555 圆柱形炉箅的§§§带有沿水平或倾斜轴旋转并在内部支持燃料的燃料支撑面 带有沿水平或倾斜轴旋转并在内部支持燃料的燃料支撑面的@@@带有可移动的燃料支撑面
555555555555555555555555 圆柱形炉箅的§§§带有沿水平或倾斜轴旋转并在内部支持燃料的燃料支撑面的@@@带有沿水平或倾斜轴旋转并在内部支持燃料的燃料支撑面的@@@带有可移动的燃料支撑面
555555555555555555555555 带有可通过燃烧区的燃料支撑面的带有专门适用于通过燃烧区推进燃料的燃料支撑面的 带有专门适用于通过燃烧区推进燃料的燃料支撑面的带有可移动的燃料支撑面
555555555555555555555555 带有可通过燃烧区的燃料支撑面的带有专门适用于通过燃烧区推进燃料的燃料支撑面的带有专门适用于通过燃烧区推进燃料的燃料支撑面的带有可移动的燃料支撑面
555555555555555555555555 链式炉箅的@@@带有可通过燃烧区的燃料支撑面的 带有可通过燃烧区的燃料支撑面的带有专门适用于通过燃烧区推进燃料的燃料支撑面的带有专门适用于通过燃烧区推进燃料的燃料支撑面的带有可移动的燃料支撑面
555555555555555555555555 链式炉箅的@@@带有可通过燃烧区的燃料支撑面的带有可通过燃烧区的燃料支撑面的带有专门适用于通过燃烧区推进燃料的燃料支撑面的带有专门适用于通过燃烧区推进燃料的燃料支撑面的带有可移动的燃料支撑面
555555555555555555555555 带有可移动且基本保持同样位置的燃料推进元件的燃料支撑面的@@@带有专门适用于通过燃烧区推进燃料的燃料支撑面的 带有专门适用于通过燃烧区推进燃料的燃料支撑面的带有可移动的燃料支撑面
555555555555555555555555 带有可移动且基本保持同样位置的燃料推进元件的燃料支撑面的@@@带有专门适用于通过燃烧区推进燃料的燃料支撑面的带有专门适

555555555555555555555555 当闭锁机或枪机在闭锁位置由凸轮或杠杆推动的撞针或击针相对于闭锁机能移动的 撞针或击针相对于闭锁机能移动的仅有可滑动地安装的击锤部件
555555555555555555555555 当闭锁机或枪机在闭锁位置由凸轮或杠杆推动的撞针或击针相对于闭锁机能移动的撞针或击针相对于闭锁机能移动的仅有可滑动地安装的击锤部件
555555555555555555555555 由受张力的弹簧推动的撞针或击针相对于闭锁机能移动的 撞针或击针相对于闭锁机能移动的仅有可滑动地安装的击锤部件
555555555555555555555555 由受张力的弹簧推动的撞针或击针相对于闭锁机能移动的撞针或击针相对于闭锁机能移动的仅有可滑动地安装的击锤部件
555555555555555555555555 用于枪机动作的枪的@@@由受张力的弹簧推动的 由受张力的弹簧推动的撞针或击针相对于闭锁机能移动的撞针或击针相对于闭锁机能移动的仅有可滑动地安装的击锤部件
555555555555555555555555 用于枪机动作的枪的@@@由受张力的弹簧推动的由受张力的弹簧推动的撞针或击针相对于闭锁机能移动的撞针或击针相对于闭锁机能移动的仅有可滑动地安装的击锤部件
555555555555555555555555 在闭锁动作的枪中的@@@由受张力的弹簧推动的 由受张力的弹簧推动的撞针或击针相对于闭锁机能移动的撞针或击针相对于闭锁机能移动的仅有可滑动地安装的击锤部件
555555555555555555555555 在闭锁动作的枪中的@@@由受张力的弹簧推动的由受张力的弹簧推动的撞针或击针相对于闭锁机能移动的撞针或击针相对于闭锁机能移动的仅有可滑动地安装的击锤部件
555555555555555555555555 通过使操作手柄回转或使杠杆相对于身管轴线产生横向运动进行闭锁的手动的 手动的闭锁元件相对于身管轴线产生旋转运动
555555555555555555555555 通过使操作手柄回转或使杠杆相对于身管轴线产生横向运动进行闭锁的手动的手动的闭锁元件相对于身管轴线产生旋转运动
555555555555555555555555 闭锁元件构成操作手柄或杆的一部分的§§§通过使操作手柄回转或使杠杆相对于身管轴线产生横向运动进行闭锁的 通过使操作手柄回转或使杠杆相对于